In [1]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
np.set_printoptions(threshold = np.nan)
def loadData():
    with np.load('notMNIST.npz') as data :
        Data, Target = data ['images'], data['labels']
        #print(Data[3745])
        #plt.figure()
        #plt.imshow(Data[3745])
        #plt.show()
        #print(Target)     # 0-9
        posClass = 2
        negClass = 9
        dataIndx = (Target==posClass) + (Target==negClass)
        #true =1 false=-1?
        #print(dataIndx)   #true or false
        #print(Data[dataIndx])  #Data[true]
        Data = Data[dataIndx]/255.
        #print(Data[0])
        Target = Target[dataIndx].reshape(-1, 1)
        #print(Target[10])
        #Target [size, 1]
        Target[Target==posClass] = 1
        Target[Target==negClass] = 0
        np.random.seed(421)
        randIndx = np.arange(len(Data))
        #print(randIndx)
        np.random.shuffle(randIndx)
        Data, Target = Data[randIndx], Target[randIndx]
        #print(Target)
        trainData, trainTarget = Data[:3500], Target[:3500]
        validData, validTarget = Data[3500:3600], Target[3500:3600]
        testData, testTarget = Data[3600:], Target[3600:]
    return trainData, validData, testData, trainTarget, validTarget, testTarget

In [2]:
def buildGraph(beta1=None, beta2=None, epsilon=None, lossType=None, learning_rate=None):
    trainData, validData, testData, trainTarget, validTarget, testTarget = loadData()
    dim_x = trainData.shape[1]
    dim_y = trainData.shape[2]

    tf.set_random_seed(421)
    W_shape = (dim_x*dim_y, 1)
    W = tf.get_variable("W", initializer=tf.truncated_normal(shape=W_shape, stddev=0.5))
    b = tf.get_variable("b", initializer=tf.truncated_normal(shape=[1], stddev=0.5))

    X = tf.placeholder(tf.float32, shape=(500, dim_x*dim_y), name="X")
    Y = tf.placeholder(tf.float32, shape=(500, 1), name="Y")
    lam = tf.placeholder(tf.float32, shape=(1, None), name="lam")

    predict = None
    loss = None
    if lossType == "MSE":
        predict = tf.matmul(X, W) + b
        loss = tf.losses.mean_squared_error(labels=Y, predictions=predict)
    elif lossType == "CE":
        logit = -1*(tf.matmul(X, W) + b)
        predict = tf.sigmoid(logit)
        loss = tf.nn.sigmoid_cross_entropy_with_logits(labels=Y, logits=logit)

    train_op = tf.train.AdamOptimizer(learning_rate=learning_rate, beta1=beta1, beta2=beta2, epsilon=epsilon).minimize(loss)

    return W, b, predict, Y, X, loss, train_op, lam

In [3]:
def SGD(batchSize, epochs):
    trainData, validData, testData, trainTarget, validTarget, testTarget = loadData()
    
    
        
    batches = trainData.shape[0]/batchSize
    print(batches)
    W, b, predict, Y, X, loss, train_op, lam = buildGraph(beta1=1, beta2=1, epsilon=0, lossType="CE", learning_rate=0.001)
    print(X.shape,Y.shape)
    SGD_train = []
    SGD_valid = []
    SGD_test = []
    W = tf.Variable(W)
    b = tf.Variable(b)
    
    with tf.Session() as sess:
        init = tf.global_variables_initializer()
        sess.run(init)
        
        
        for i in range(epochs):
            rand_i = np.random.choice(100, size=batchSize)

            x_batch = trainData[rand_i].reshape((batchSize, trainData.shape[1]*trainData.shape[2]))
            y_batch = trainTarget[rand_i].reshape((batchSize, 1))
            print(x_batch.shape)
            print(y_batch.shape)
            _, c = sess.run([train_op, loss], feed_dict={X:x_batch, Y:y_batch})
            print(_,c)
            #print("SGD training error:  ",sess.run([train_op,loss], feed_dict={X:x_batch, Y:y_batch}))
        #sess.close()
        
    return

In [4]:
SGD(500,700)

7.0
(500, 784) (500, 1)
(500, 784)
(500, 1)
None [[1.43294060e+00]
 [6.85377698e-03]
 [5.94870150e-01]
 [6.45283842e-04]
 [5.94870150e-01]
 [2.12592278e-02]
 [1.43294060e+00]
 [6.29391149e-03]
 [1.14417398e-05]
 [1.29701227e-01]
 [1.75755849e-06]
 [1.25860423e-03]
 [1.79395766e-03]
 [1.25860423e-03]
 [1.79395766e-03]
 [4.87529755e-01]
 [2.87975520e-01]
 [3.30159545e-01]
 [2.43510026e-03]
 [1.29701227e-01]
 [2.01386023e+00]
 [1.75755849e-06]
 [8.69691503e-05]
 [1.60945319e-02]
 [5.79819025e-04]
 [7.92135106e-05]
 [4.82001528e-03]
 [2.75221746e-03]
 [1.08646281e-01]
 [2.07831559e-04]
 [1.52298305e-02]
 [8.69691503e-05]
 [4.59140097e-07]
 [2.05181376e-03]
 [2.07831559e-04]
 [4.81738329e-01]
 [1.43294060e+00]
 [1.47497868e-02]
 [5.72633362e-05]
 [4.39274072e-06]
 [1.87532932e-01]
 [1.67729780e-02]
 [5.81103265e-01]
 [1.75686277e-04]
 [4.39274072e-06]
 [5.26789459e-04]
 [1.14352988e-04]
 [2.12981875e-04]
 [1.80932656e-02]
 [1.14352988e-04]
 [1.43294060e+00]
 [7.11212754e-02]
 [4.96590048e-0